# Visualizing Mapillary Data on GCP

This short notebook demostrates how we can access and visualize data was imported from Mapillary and stored on CGP.


### Authenticating with Google Cloud

Before we can run this notebook on a new device, we will have to authenticate with google cloud. To do so, please run the following command in a terminal window (you shouldn't need to do this if you have already authenticated on this device):

```
gcloud auth application-default login 
```

Now we can continue with importing the python modules that we will use.

In [1]:
import folium
import numpy as np

from src.controller import MapillaryImage
from src.visualizer import Visualize

## Setting Environmental Variables

In order for the importer module to access both Google Storage and the Mapillary API, the following environmental variables must be set. Replace the text in `<>` with actual variables before running the next block.

In [2]:
%env DATABASE_URL=<database_url>

env: DATABASE_URL=postgresql://admin:NKbu5:$c7QyA{+-Z@104.198.127.192:5432/mapillary


## Get Data from Database by Bounding Box

In order to visualize the data, we will need to query the database and have the data in a Python data type. The `MapillaryImage` controller class contains functions to return data from the database in various formats. We will use it to construct a Geopandas dataframe of data that falls within some bounding box of interest.

First, initialize the controller:

In [3]:
imgs = MapillaryImage()

Then, set parameters:

In [9]:
bbox = [141.028,42.292,141.121,42.444]

Now, fetch the data:

In [10]:
data = imgs.select_within_bbox(bbox)

We can observe the total number of rows of the data and take a look at the first few rows:

In [11]:
print(f"The number of rows returned is: {len(data.index)}")
data.head()

The number of rows returned is: 1624


id                             seq  altitude  \
0  1316223008780318  4EDJVt3TmnW1hALm7SARrA            31.231   
1  3940805029337923  oahj3avp62i9333f14wq1b            27.290   
2   154327626587614  hxr4j9v5oazg96041bimr8            30.454   
3   476773713544002  4EDJVt3TmnW1hALm7SARrA            33.879   
4   803271957055341  4EDJVt3TmnW1hALm7SARrA            33.856   

   computed_altitude                                  camera_parameters  \
0           2.027818  [1.5235641673935, 0.087075630916789, 0.0063187...   
1           2.003059  [0.43952642366, 0.0607931433091, 0.00047321287...   
2           3.926726  [0.79644495704815, 0.11606791047681, 0.0402876...   
3           2.412898  [0.49681125152212, 0.14647653933878, 0.0689683...   
4           2.435879  [0.49681125152212, 0.14647653933878, 0.0689683...   

  camera_type               captured_at  compass_angle  \
0     fisheye 2019-10-23 14:53:03+00:00       36.03959   
1     fisheye 2019-10-22 11:43:09+00:00      215.11337   
2     fisheye 2019-10-23 14:23:07+00:00      321.71810   
3     fisheye 2019-10-23 14:50:24+00:00      141.03300   
4     fisheye 2019-10-23 14:50:23+00:00      142.48012   

   computed_compass_angle exif_orientation             merge_cc  \
0               36.750816                3  2730694295095799808   
1              215.920180                3  2730694295095799808   
2              324.158800                3  1699003678672699904   
3              146.524610                3  1699003678672699904   
4              147.678100                3  1699003678672699904   

                                                mesh  \
0  {'id': '488440382603236', 'url': 'https://scon...   
1                                               None   
2  {'id': '849892375616988', 'url': 'https://scon...   
3  {'id': '2564358967203782', 'url': 'https://sco...   
4  {'id': '533828757624761', 'url': 'https://scon...   

                                         sfm_cluster  \
0  {'id': '528674084929883', 'url': 'https://scon...   
1                         {'id': '1167304573740719'}   
2  {'id': '484032509534216', 'url': 'https://scon...   
3  {'id': '233453788582178', 'url': 'https://scon...   
4  {'id': '233453788582178', 'url': 'https://scon...   

                                          detections  \
0  {'data': [{'id': '1318687751867177'}, {'id': '...   
1  {'data': [{'id': '3949982768420149'}, {'id': '...   
2  {'data': [{'id': '155103619843348'}, {'id': '1...   
3  {'data': [{'id': '478803163341057'}, {'id': '4...   
4              {'data': [{'id': '805369486845588'}]}   

                                           image_url  \
0  https://storage.cloud.google.com/sudb_images/i...   
1  https://storage.cloud.google.com/sudb_images/i...   
2  https://storage.cloud.google.com/sudb_images/i...   
3  https://storage.cloud.google.com/sudb_images/i...   
4  https://storage.cloud.google.com/sudb_images/i...   

                                   computed_geometry  \
0  0101000020E610000095490436C3A16140F466DADF502E...   
1  0101000020E6100000F266351B9BA16140A5A13B3EA82D...   
2  0101000020E6100000154997283DA1614086A3EA1E812E...   
3  0101000020E61000004B7D6F9355A16140CDE35240272E...   
4  0101000020E6100000FF4450E654A16140A77F6DE6292E...   

                     geometry  
0  POINT (141.05508 42.36184)  
1  POINT (141.05018 42.35670)  
2  POINT (141.03872 42.36332)  
3  POINT (141.04169 42.36057)  
4  POINT (141.04161 42.36065)

## Visualize Data

We will use the `Visualize` class and folium maps to visualize the data. Before we can get started, we must initialize the Visualize class:

In [12]:
vis = Visualize(data)

Now we can map the locations of each image. We will make use of the simple Visualizer popup generator function to add popups that have images and basic metadata when markers are clicked.

In [13]:
map = folium.Map(location=[42.35849, 141.01552], tiles="OpenStreetMap", zoom_start=18)

images = [[point.xy[1][0], point.xy[0][0]] for point in data.geometry]

for i, coordinates in enumerate(images):
    html = vis.popup_html(i)
    popup = folium.Popup(folium.Html(html, script=True), max_width=500)
    map.add_child(
        folium.Marker(
            location=coordinates,
            popup=popup,
            icon=folium.Icon(),
        )
    )
 
map

Note that the bounding box should be small if mapping all features. Otherwise the map will render poorly. As a rule of thumb, try to keep this number less than 5000 or so.

## Get data and Visualize by Image ID or Sequence ID

We can also select data from GCP by image ID or sequence ID. While it is also possible to filter data using geopandas on the earlier tables, there may be times where filtering on the database directly can be more efficient. 

The following blocks demonstrate how this is done:

In [4]:
data_by_id = imgs.select_by_image_id(163679945611763)

data_by_id

id                             seq  altitude  \
0  163679945611763  vSDgMY3PXlEz6wLvvUcoCQ            44.829   

   computed_altitude                                  camera_parameters  \
0           2.603053  [0.48891904064413, 0.20888950293583, 0.1219989...   

  camera_type               captured_at  compass_angle  \
0     fisheye 2019-10-23 09:32:31+00:00       349.3094   

   computed_compass_angle exif_orientation            merge_cc  \
0               344.35077                3  363421436348230016   

                                                mesh  \
0  {'id': '144616154353630', 'url': 'https://scon...   

                                         sfm_cluster detections  \
0  {'id': '693012121489801', 'url': 'https://scon...       None   

                                           image_url  \
0  https://storage.cloud.google.com/sudb_images/i...   

                                   computed_geometry  \
0  0101000020E610000003EB972A80A061407C6D3F31D02D...   

                     geometry  
0  POINT (141.01564 42.35792)

Now visualize:

In [18]:
vis = Visualize(data_by_id)

x = data_by_id.geometry[0].xy[0][0]
y = data_by_id.geometry[0].xy[1][0]

map = folium.Map(location=[y, x], tiles="OpenStreetMap", zoom_start=18)

html = vis.popup_html(0)
popup = folium.Popup(folium.Html(html, script=True), max_width=500)

map.add_child(
    folium.Marker(
        location=[y, x],
        popup=popup,
        icon=folium.Icon(),
    )
)

map

We can repeat the above for a sequence:

In [6]:
data_by_seq = imgs.select_by_sequence_id('vSDgMY3PXlEz6wLvvUcoCQ')

print(f"The number of rows returned is: {len(data_by_seq.index)}")
data_by_seq.head()

The number of rows returned is: 229


id                             seq  altitude  \
0   804730633805031  vSDgMY3PXlEz6wLvvUcoCQ            40.196   
1   500240141017461  vSDgMY3PXlEz6wLvvUcoCQ            70.255   
2   787355605248745  vSDgMY3PXlEz6wLvvUcoCQ            36.020   
3  1180474129086959  vSDgMY3PXlEz6wLvvUcoCQ            41.042   
4   804124637170637  vSDgMY3PXlEz6wLvvUcoCQ            64.850   

   computed_altitude                                  camera_parameters  \
0          -0.104864  [0.63925377089732, 0.16873569857158, 0.0646424...   
1           2.229935  [0.48891904064413, 0.20888950293583, 0.1219989...   
2           2.204050  [0.48788902678999, 0.29209408835279, 0.1799471...   
3           2.564447  [0.63925377089732, 0.16873569857158, 0.0646424...   
4           1.917214  [0.48891904064413, 0.20888950293583, 0.1219989...   

  camera_type               captured_at  compass_angle  \
0     fisheye 2019-10-23 09:31:47+00:00      324.86017   
1     fisheye 2019-10-23 09:33:01+00:00      358.90268   
2     fisheye 2019-10-23 09:30:05+00:00        9.44350   
3     fisheye 2019-10-23 09:32:03+00:00      351.24810   
4     fisheye 2019-10-23 09:32:56+00:00      352.01395   

   computed_compass_angle exif_orientation             merge_cc  \
0              318.918850                3   363421436348230016   
1              352.995670                3   363421436348230016   
2                3.972956                3  2836489071609600000   
3              342.962000                3   363421436348230016   
4              346.417420                3   363421436348230016   

                                                mesh  \
0  {'id': '210491744020899', 'url': 'https://scon...   
1  {'id': '378513040151689', 'url': 'https://scon...   
2  {'id': '474555073830961', 'url': 'https://scon...   
3  {'id': '412314203100517', 'url': 'https://scon...   
4  {'id': '2864818760403473', 'url': 'https://sco...   

                                         sfm_cluster  \
0  {'id': '2993341374283221', 'url': 'https://sco...   
1  {'id': '693012121489801', 'url': 'https://scon...   
2  {'id': '2944530062492340', 'url': 'https://sco...   
3  {'id': '2993341374283221', 'url': 'https://sco...   
4  {'id': '693012121489801', 'url': 'https://scon...   

                                          detections  \
0              {'data': [{'id': '807023293575765'}]}   
1              {'data': [{'id': '502402347467907'}]}   
2  {'data': [{'id': '788735198444119'}, {'id': '7...   
3  {'data': [{'id': '1183164155484623'}, {'id': '...   
4              {'data': [{'id': '806681890248245'}]}   

                                           image_url  \
0  https://storage.cloud.google.com/sudb_images/i...   
1  https://storage.cloud.google.com/sudb_images/i...   
2  https://storage.cloud.google.com/sudb_images/i...   
3  https://storage.cloud.google.com/sudb_images/i...   
4  https://storage.cloud.google.com/sudb_images/i...   

                                   computed_geometry  \
0  0101000020E61000009A772B7284A0614029EC602EAD2D...   
1  0101000020E6100000566987787BA06140A71A42C4292E...   
2  0101000020E61000003FD86E40A7A06140CC721FA9EE2C...   
3  0101000020E6100000FEDB76BF80A06140C3E94309C72D...   
4  0101000020E6100000DB7760ED7BA06140D404F7101A2E...   

                     geometry  
0  POINT (141.01617 42.35684)  
1  POINT (141.01507 42.36065)  
2  POINT (141.02042 42.35103)  
3  POINT (141.01572 42.35763)  
4  POINT (141.01513 42.36017)

And visualizing:

In [8]:
vis = Visualize(data_by_seq)

x = data_by_seq.geometry[0].xy[0][0]
y = data_by_seq.geometry[0].xy[1][0]

map = folium.Map(location=[y, x], tiles="OpenStreetMap", zoom_start=18)

images = [[point.xy[1][0], point.xy[0][0]] for point in data_by_seq.geometry]

for i, coordinates in enumerate(images):
    html = vis.popup_html(i)
    popup = folium.Popup(folium.Html(html, script=True), max_width=500)
    map.add_child(
        folium.Marker(
            location=coordinates,
            popup=popup,
            icon=folium.Icon(),
        )
    )
 
map

## Download Image

Finally, it is also possible to download an image from GCP storage to your local device. To do this, you need to know the image_url from the database and supply a path to where on your device you want to save your image.

Using our queried image by ID from earlier; first set the desired download directory:

In [6]:
download_dir = '/Users/iosefa/Downloads'

SyntaxError: invalid syntax (1289229089.py, line 1)

In [5]:
image_url = data_by_id['image_url'][0]
image_path = image_url.split('.com/')[1]
image_name = image_path.split('/')[-1]

bucket_name = image_path.split('/')[0]
rel_path = image_path.split('/')[1:]

imgs.download_gcp_image(image_path, f'{}/{image_name}')